In [62]:
# from google.colab import drive
# drive.mount('/content/drive')

In [63]:
# cd /content/drive/My Drive/University/SEM7/CS4622_Machine_Learning/Project_1/Fair_Classification

# Imports

In [64]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
import calendar
import warnings
from math import sin, cos, sqrt, atan2, radians,asin

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestRegressor
# import lightgbm as lgb
# import xgboost as xgb
from sklearn.metrics import roc_auc_score
# from hyperopt import hp, fmin, tpe, STATUS_OK, Trials
warnings.filterwarnings('ignore')
# from xgboost import XGBClassifier
from sklearn.metrics import accuracy_score,f1_score


# Load Data

In [65]:
# train=pd.read_csv("/content/drive/My Drive/University/SEM7/CS4622_Machine_Learning/Project_1/Fair_Classification/features/Train_FeatureEngineering_4_without_droping_any_feature.csv")
# test=pd.read_csv("/content/drive/My Drive/University/SEM7/CS4622_Machine_Learning/Project_1/Fair_Classification/features/Test_FeatureEngineering_4.csv")
# for other account
train=pd.read_csv("features/6_Train_FeatureEngineering_fill_null_with_-1.csv")
test=pd.read_csv("features/6_Test_FeatureEngineering_fill_null_with_-1.csv")

print("Shape of Training Data",train.shape)
print("Shape of Testing Data", test.shape)


Shape of Training Data (17176, 25)
Shape of Testing Data (8576, 24)


In [66]:
train.columns

Index(['tripid', 'additional_fare', 'duration', 'meter_waiting',
       'meter_waiting_fare', 'meter_waiting_till_pickup', 'pickup_time',
       'drop_time', 'pick_lat', 'pick_lon', 'drop_lat', 'drop_lon', 'fare',
       'label', 'additional_fare_is_outlier', 'meter_waiting_fare_is_outlier',
       'fare_is_outlier', 'pickup_date', 'pickup_day', 'pickup_hour',
       'pickup_day_of_week', 'pickup_month', 'pickup_year', 'is_outlier_loc',
       'trip_distance'],
      dtype='object')

In [67]:
test.columns

Index(['tripid', 'additional_fare', 'duration', 'meter_waiting',
       'meter_waiting_fare', 'meter_waiting_till_pickup', 'pickup_time',
       'drop_time', 'pick_lat', 'pick_lon', 'drop_lat', 'drop_lon', 'fare',
       'additional_fare_is_outlier', 'meter_waiting_fare_is_outlier',
       'fare_is_outlier', 'pickup_date', 'pickup_day', 'pickup_hour',
       'pickup_day_of_week', 'pickup_month', 'pickup_year', 'is_outlier_loc',
       'trip_distance'],
      dtype='object')

# Data_Preprocessing

In [68]:
# drop_columns_train=['tripid','pickup_time','drop_time','pick_lat','pick_lon','drop_lat','drop_lon','pickup_date','pickup_latitude_round3','pickup_longitude_round3','dropoff_latitude_round3','dropoff_longitude_round3']
# drop_columns_test=['tripid','pickup_time','drop_time','pick_lat','pick_lon','drop_lat','drop_lon','pickup_date','pickup_latitude_round3','pickup_longitude_round3','dropoff_latitude_round3','dropoff_longitude_round3','is_outlier_loc']

drop_columns_train=['tripid','pickup_time','drop_time','pickup_date','pickup_day','pickup_month','pickup_year']
drop_columns_test=['tripid','pickup_time','drop_time','pickup_date','pickup_day','pickup_month','pickup_year']

In [69]:
train_1=train.drop(drop_columns_train,axis=1)
test_1=test.drop(drop_columns_test,axis=1)
print("Shape of Training Data after dropping columns",train_1.shape)
print("Shape of Testing Data after dropping columns",test_1.shape)

Shape of Training Data after dropping columns (17176, 18)
Shape of Testing Data after dropping columns (8576, 17)


In [70]:
# def encodeDays(day_of_week):
#   day_dict={'Sunday':0,'Monday':1,'Tuesday':2,'Wednesday':3,'Thursday':4,'Friday':5,'Saturday':6}
#   return day_dict[day_of_week]
# def encodeLabel(label):
#   label_dict={'correct':1,'incorrect':0}
#   return label_dict[label]
# def clean_data(data,isTrain):
#   data['pickup_day_of_week']=data['pickup_day_of_week'].apply(lambda x:encodeDays(x))
#   if(isTrain):
#     data['label']=data['label'].apply(lambda x:encodeLabel(x))
#   return data

# train_1=clean_data(train_1,True)
# test_1=clean_data(test_1,False)
# print("Shape of Training Data after cleaning ",train_1.shape)
# print("Shape of Testing Data after cleaning", test_1.shape)

In [71]:
test_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8576 entries, 0 to 8575
Data columns (total 17 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   additional_fare                8576 non-null   float64
 1   duration                       8576 non-null   int64  
 2   meter_waiting                  8576 non-null   int64  
 3   meter_waiting_fare             8576 non-null   float64
 4   meter_waiting_till_pickup      8576 non-null   int64  
 5   pick_lat                       8576 non-null   float64
 6   pick_lon                       8576 non-null   float64
 7   drop_lat                       8576 non-null   float64
 8   drop_lon                       8576 non-null   float64
 9   fare                           8576 non-null   float64
 10  additional_fare_is_outlier     8576 non-null   int64  
 11  meter_waiting_fare_is_outlier  8576 non-null   int64  
 12  fare_is_outlier                8576 non-null   i

In [72]:
columns_titles = ['additional_fare','duration','meter_waiting','meter_waiting_fare','meter_waiting_till_pickup','pick_lat','pick_lon','drop_lat','drop_lon','fare','additional_fare_is_outlier','meter_waiting_fare_is_outlier','fare_is_outlier','pickup_hour','pickup_day_of_week','is_outlier_loc','trip_distance','label']
train_1=train_1.reindex(columns=columns_titles)
train_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17176 entries, 0 to 17175
Data columns (total 18 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   additional_fare                17176 non-null  float64
 1   duration                       17176 non-null  float64
 2   meter_waiting                  17176 non-null  float64
 3   meter_waiting_fare             17176 non-null  float64
 4   meter_waiting_till_pickup      17176 non-null  float64
 5   pick_lat                       17176 non-null  float64
 6   pick_lon                       17176 non-null  float64
 7   drop_lat                       17176 non-null  float64
 8   drop_lon                       17176 non-null  float64
 9   fare                           17176 non-null  float64
 10  additional_fare_is_outlier     17176 non-null  int64  
 11  meter_waiting_fare_is_outlier  17176 non-null  int64  
 12  fare_is_outlier                17176 non-null 

In [73]:
categorical_var = ['additional_fare_is_outlier','meter_waiting_fare_is_outlier','fare_is_outlier','pickup_hour','pickup_day_of_week','is_outlier_loc'] 
categorical_var_indices = [train_1.columns.get_loc(c) for c in categorical_var if c in train_1]
print('\nCategorical Variables indices : ',categorical_var_indices)


Categorical Variables indices :  [10, 11, 12, 13, 14, 15]


In [74]:
train_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17176 entries, 0 to 17175
Data columns (total 18 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   additional_fare                17176 non-null  float64
 1   duration                       17176 non-null  float64
 2   meter_waiting                  17176 non-null  float64
 3   meter_waiting_fare             17176 non-null  float64
 4   meter_waiting_till_pickup      17176 non-null  float64
 5   pick_lat                       17176 non-null  float64
 6   pick_lon                       17176 non-null  float64
 7   drop_lat                       17176 non-null  float64
 8   drop_lon                       17176 non-null  float64
 9   fare                           17176 non-null  float64
 10  additional_fare_is_outlier     17176 non-null  int64  
 11  meter_waiting_fare_is_outlier  17176 non-null  int64  
 12  fare_is_outlier                17176 non-null 

In [75]:
# train_1=pd.get_dummies(train_1)
# test_1=pd.get_dummies(test_1)

# print("Shape of Training Data after One Hot Encoding",train_1.shape)
# print("Shape of Testing Data after One Hot Encoding",test_1.shape)

In [76]:
# print('Old size: %d' % len(train))
# train_1 = train_1.dropna()
# print('New size: %d' % len(train))

In [77]:
X=train_1.drop(['label'],axis=1)
y=train_1['label']

In [78]:
#split data into train and validation data
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size=0.2)
print("Number of records in training data ",X_train.shape[0])
print("Number of records in validation data ",X_test.shape[0])

Number of records in training data  13740
Number of records in validation data  3436


# Classifiers

## XGBoost CLassifier

In [79]:
# model = XGBClassifier()
# model.fit(X_train, y_train)

## Linear Regression Classifier

In [80]:
# model = LinearRegression()
# model.fit(X_train,y_train)
# # y_pred=model.predict(X_test)
# # lm_rmse=np.sqrt(mean_squared_error(y_pred, y_test))
# # print("RMSE for Linear Regression is ",lm_rmse)


## LGBM Classifier

In [81]:
# estimator = lgb.LGBMClassifier(learning_rate = 0.125, metric = 'l1', 
#                         n_estimators = 20, num_leaves = 38)


# param_grid = {
#     'n_estimators': [x for x in range(24,40,2)],
#     'learning_rate': [0.10, 0.125, 0.15, 0.175, 0.2]}
# gridsearch = GridSearchCV(estimator, param_grid)

# gridsearch.fit(X_train, y_train,
#         eval_set = [(X_test, y_test)],
#         eval_metric = ['auc', 'binary_logloss'],
#         early_stopping_rounds = 5)

In [82]:
# gbm = lgb.LGBMClassifier(boosting_type='gbdt', class_weight=None,
#                                       colsample_bytree=1.0,
#                                       importance_type='split',
#                                       learning_rate=0.125, max_depth=-1,
#                                       metric='l1', min_child_samples=20,
#                                       min_child_weight=0.001,
#                                       min_split_gain=0.0, n_estimators=20,
#                                       n_jobs=-1, num_leaves=38, objective=None,
#                                       random_state=None, reg_alpha=0.0,
#                                       reg_lambda=0.0, silent=True,
#                                       subsample=1.0, subsample_for_bin=200000,
#                                       subsample_freq=0)


# gbm.fit(X, y,
#         eval_set=[(X_test, y_test)],
#         eval_metric=['auc', 'binary_logloss'],
# early_stopping_rounds=5)

In [83]:
# ax = lgb.plot_importance(gbm, height = 0.4, 
#                          max_num_features = 50, 
#                          xlim = (0,100), ylim = (0,23), 
#                          figsize = (10,6))
# plt.show()

In [84]:
# sorted(gbm.feature_importances_,reverse=True)

In [85]:

# # The code below aims to drop  to keep the features that are included in the most important features. 
# temp = 0 
# total = sum(gbm.feature_importances_)
# for feature in sorted(gbm.feature_importances_, reverse=True):
#     temp+=feature
#     print(feature)
#     if temp/total >= 0.85:
#         print(feature,temp/total) # stop when we 
#         break

In [86]:
# #The above means let go of all variables after PAY_AMT_5
# y_pred_prob = gbm.predict_proba(test_1)[:, 1]
# # auc_roc_0 = str(roc_auc_score(y_test, y_pred_prob)) # store AUC score without dimensionality reduction
# # print('AUC without dimensionality reduction: \n' + auc_roc_0)

In [87]:
X

additional_fare  duration  meter_waiting  meter_waiting_fare  \
0                 10.5     834.0           56.0              0.0000   
1                 10.5     791.0           47.0              0.0000   
2                 10.5    1087.0           80.0              0.0000   
3                 10.5     598.0          271.0             15.6638   
4                 -1.0      -1.0           -1.0             -1.0000   
...                ...       ...            ...                 ...   
17171             10.5     838.0           93.0              5.4219   
17172             10.5    2151.0          428.0              0.0000   
17173             10.5     263.0            9.0              0.0000   
17174             10.5     858.0          115.0              0.0000   
17175             10.5     262.0           21.0              1.2243   

       meter_waiting_till_pickup  pick_lat  pick_lon  drop_lat  drop_lon  \
0                           64.0   6.86252   79.8993   6.90330   79.8783   
1                          134.0   6.88589   79.8984   6.91373   79.8923   
2                           61.0   6.90839   79.8651   6.93669   79.9146   
3                           68.0   6.92570   79.8895   6.92748   79.8971   
4                           -1.0   6.87441   79.8615   6.84478   79.9290   
...                          ...       ...       ...       ...       ...   
17171                      451.0   7.29073   80.6367   7.28891   80.6557   
17172                       39.0   6.90569   79.8516   6.95089   79.9389   
17173                      110.0   7.09210   79.9000   7.10135   79.9017   
17174                      317.0   6.94540   79.8768   6.93574   79.9010   
17175                       23.0   6.90257   79.9557   6.90823   79.9374   

         fare  additional_fare_is_outlier  meter_waiting_fare_is_outlier  \
0      270.32                           0                              0   
1      197.85                           0                              0   
2      301.64                           0                              0   
3       82.30                           0                              0   
4      358.39                           1                              1   
...       ...                         ...                            ...   
17171  198.26                           0                              0   
17172  581.23                           0                              0   
17173   76.20                           0                              0   
17174  133.31                           0                              0   
17175   98.57                           0                              0   

       fare_is_outlier  pickup_hour  pickup_day_of_week  is_outlier_loc  \
0                    0            0                   5               0   
1                    0            0                   5               0   
2                    0            1                   5               0   
3                    0            2                   5               0   
4                    0            3                   5               0   
...                ...          ...                 ...             ...   
17171                0           22                   5               0   
17172                0           23                   5               0   
17173                0           23                   5               0   
17174                0           23                   5               0   
17175                0           23                   5               0   

       trip_distance  
0           3.164501  
1           1.968540  
2           3.917991  
3           0.535588  
4           5.062797  
...              ...  
17171       1.308220  
17172       6.753297  
17173       0.649655  
17174       1.788975  
17175       1.314744  

[17176 rows x 17 columns]

In [88]:
# #We can choose to drop the last 6 features from in our new model to reduce dimensionality, and thus save training time and space

# X = X_train.drop(['additional_fare','pickup_day_of_week','pickup_month','pickup_day'], axis=1)

## CatBoost

In [89]:
# !pip install catboost

In [90]:
from catboost import CatBoostClassifier

model = CatBoostClassifier(iterations=100000, 
                           cat_features=categorical_var_indices, 
#                            task_type="GPU",
                           devices='0:1')
model.fit(X,
          y,
          verbose=True)




Learning rate set to 0.000508
0:	learn: 0.6925921	total: 47.3ms	remaining: 1h 18m 46s
1:	learn: 0.6920084	total: 97.8ms	remaining: 1h 21m 30s
2:	learn: 0.6913799	total: 145ms	remaining: 1h 20m 27s
3:	learn: 0.6907891	total: 202ms	remaining: 1h 24m 6s
4:	learn: 0.6902486	total: 268ms	remaining: 1h 29m 21s
5:	learn: 0.6896686	total: 360ms	remaining: 1h 39m 52s
6:	learn: 0.6891493	total: 457ms	remaining: 1h 48m 46s
7:	learn: 0.6886416	total: 555ms	remaining: 1h 55m 38s
8:	learn: 0.6880562	total: 653ms	remaining: 2h 50s
9:	learn: 0.6874177	total: 741ms	remaining: 2h 3m 33s
10:	learn: 0.6868395	total: 819ms	remaining: 2h 4m 7s
11:	learn: 0.6862992	total: 900ms	remaining: 2h 4m 58s
12:	learn: 0.6857215	total: 975ms	remaining: 2h 4m 57s
13:	learn: 0.6852060	total: 1.04s	remaining: 2h 4m 1s
14:	learn: 0.6846793	total: 1.13s	remaining: 2h 5m 32s
15:	learn: 0.6840727	total: 1.22s	remaining: 2h 7m 28s
16:	learn: 0.6834461	total: 1.32s	remaining: 2h 9m 11s
17:	learn: 0.6828919	total: 1.4s	remainin

151:	learn: 0.6130581	total: 11.2s	remaining: 2h 3m 7s
152:	learn: 0.6126136	total: 11.3s	remaining: 2h 3m 9s
153:	learn: 0.6120691	total: 11.4s	remaining: 2h 3m 4s
154:	learn: 0.6115823	total: 11.5s	remaining: 2h 2m 59s
155:	learn: 0.6110473	total: 11.5s	remaining: 2h 2m 50s
156:	learn: 0.6106302	total: 11.6s	remaining: 2h 2m 42s
157:	learn: 0.6101167	total: 11.7s	remaining: 2h 2m 46s
158:	learn: 0.6096853	total: 11.7s	remaining: 2h 2m 42s
159:	learn: 0.6092870	total: 11.8s	remaining: 2h 2m 34s
160:	learn: 0.6087987	total: 11.9s	remaining: 2h 2m 31s
161:	learn: 0.6082788	total: 11.9s	remaining: 2h 2m 31s
162:	learn: 0.6078530	total: 12s	remaining: 2h 2m 34s
163:	learn: 0.6073040	total: 12.1s	remaining: 2h 2m 41s
164:	learn: 0.6068702	total: 12.2s	remaining: 2h 2m 44s
165:	learn: 0.6064593	total: 12.3s	remaining: 2h 2m 53s
166:	learn: 0.6060447	total: 12.3s	remaining: 2h 2m 39s
167:	learn: 0.6055918	total: 12.4s	remaining: 2h 2m 38s
168:	learn: 0.6050846	total: 12.4s	remaining: 2h 2m 3

301:	learn: 0.5482618	total: 22.2s	remaining: 2h 2m 3s
302:	learn: 0.5478414	total: 22.3s	remaining: 2h 2m 1s
303:	learn: 0.5475221	total: 22.3s	remaining: 2h 1m 53s
304:	learn: 0.5472028	total: 22.3s	remaining: 2h 1m 40s
305:	learn: 0.5468801	total: 22.4s	remaining: 2h 1m 30s
306:	learn: 0.5465470	total: 22.4s	remaining: 2h 1m 28s
307:	learn: 0.5461107	total: 22.5s	remaining: 2h 1m 25s
308:	learn: 0.5457564	total: 22.6s	remaining: 2h 1m 26s
309:	learn: 0.5453224	total: 22.7s	remaining: 2h 1m 30s
310:	learn: 0.5449846	total: 22.7s	remaining: 2h 1m 32s
311:	learn: 0.5446105	total: 22.8s	remaining: 2h 1m 37s
312:	learn: 0.5441410	total: 22.9s	remaining: 2h 1m 35s
313:	learn: 0.5438219	total: 22.9s	remaining: 2h 1m 23s
314:	learn: 0.5434156	total: 23s	remaining: 2h 1m 22s
315:	learn: 0.5430756	total: 23.1s	remaining: 2h 1m 23s
316:	learn: 0.5426715	total: 23.2s	remaining: 2h 1m 23s
317:	learn: 0.5423541	total: 23.2s	remaining: 2h 1m 9s
318:	learn: 0.5419536	total: 23.3s	remaining: 2h 1m 8

452:	learn: 0.4949880	total: 32.1s	remaining: 1h 57m 23s
453:	learn: 0.4946221	total: 32.1s	remaining: 1h 57m 22s
454:	learn: 0.4942458	total: 32.2s	remaining: 1h 57m 23s
455:	learn: 0.4939738	total: 32.2s	remaining: 1h 57m 19s
456:	learn: 0.4936321	total: 32.3s	remaining: 1h 57m 20s
457:	learn: 0.4932866	total: 32.4s	remaining: 1h 57m 24s
458:	learn: 0.4929167	total: 32.5s	remaining: 1h 57m 27s
459:	learn: 0.4925801	total: 32.6s	remaining: 1h 57m 27s
460:	learn: 0.4922939	total: 32.6s	remaining: 1h 57m 25s
461:	learn: 0.4919176	total: 32.7s	remaining: 1h 57m 23s
462:	learn: 0.4915436	total: 32.8s	remaining: 1h 57m 22s
463:	learn: 0.4911665	total: 32.8s	remaining: 1h 57m 24s
464:	learn: 0.4909077	total: 32.9s	remaining: 1h 57m 16s
465:	learn: 0.4905987	total: 33s	remaining: 1h 57m 19s
466:	learn: 0.4903195	total: 33s	remaining: 1h 57m 14s
467:	learn: 0.4900537	total: 33.1s	remaining: 1h 57m 12s
468:	learn: 0.4897149	total: 33.2s	remaining: 1h 57m 15s
469:	learn: 0.4894239	total: 33.2s	

600:	learn: 0.4510868	total: 42.1s	remaining: 1h 56m 2s
601:	learn: 0.4508474	total: 42.2s	remaining: 1h 56m 1s
602:	learn: 0.4505310	total: 42.2s	remaining: 1h 56m
603:	learn: 0.4502984	total: 42.3s	remaining: 1h 55m 56s
604:	learn: 0.4500832	total: 42.3s	remaining: 1h 55m 53s
605:	learn: 0.4497768	total: 42.4s	remaining: 1h 55m 52s
606:	learn: 0.4495631	total: 42.4s	remaining: 1h 55m 45s
607:	learn: 0.4492480	total: 42.5s	remaining: 1h 55m 44s
608:	learn: 0.4489372	total: 42.5s	remaining: 1h 55m 43s
609:	learn: 0.4486530	total: 42.6s	remaining: 1h 55m 41s
610:	learn: 0.4484022	total: 42.6s	remaining: 1h 55m 37s
611:	learn: 0.4481679	total: 42.7s	remaining: 1h 55m 34s
612:	learn: 0.4478573	total: 42.8s	remaining: 1h 55m 33s
613:	learn: 0.4475914	total: 42.8s	remaining: 1h 55m 32s
614:	learn: 0.4472709	total: 42.9s	remaining: 1h 55m 30s
615:	learn: 0.4470130	total: 43s	remaining: 1h 55m 30s
616:	learn: 0.4467925	total: 43s	remaining: 1h 55m 27s
617:	learn: 0.4465130	total: 43.1s	remain

...

99288:	learn: 0.0756730	total: 1h 49m 9s	remaining: 46.9s
99289:	learn: 0.0756727	total: 1h 49m 9s	remaining: 46.8s
99290:	learn: 0.0756720	total: 1h 49m 9s	remaining: 46.8s
99291:	learn: 0.0756719	total: 1h 49m 9s	remaining: 46.7s
99292:	learn: 0.0756708	total: 1h 49m 9s	remaining: 46.6s
99293:	learn: 0.0756701	total: 1h 49m 9s	remaining: 46.6s
99294:	learn: 0.0756695	total: 1h 49m 9s	remaining: 46.5s
99295:	learn: 0.0756687	total: 1h 49m 9s	remaining: 46.4s
99296:	learn: 0.0756684	total: 1h 49m 9s	remaining: 46.4s
99297:	learn: 0.0756674	total: 1h 49m 9s	remaining: 46.3s
99298:	learn: 0.0756670	total: 1h 49m 9s	remaining: 46.2s
99299:	learn: 0.0756663	total: 1h 49m 9s	remaining: 46.2s
99300:	learn: 0.0756661	total: 1h 49m 9s	remaining: 46.1s
99301:	learn: 0.0756660	total: 1h 49m 9s	remaining: 46s
99302:	learn: 0.0756651	total: 1h 49m 9s	remaining: 46s
99303:	learn: 0.0756650	total: 1h 49m 10s	remaining: 45.9s
99304:	learn: 0.0756645	total: 1h 49m 10s	remaining: 45.8s
99305:	learn: 0.

99431:	learn: 0.0756047	total: 1h 49m 15s	remaining: 37.4s
99432:	learn: 0.0756046	total: 1h 49m 15s	remaining: 37.4s
99433:	learn: 0.0756040	total: 1h 49m 15s	remaining: 37.3s
99434:	learn: 0.0756035	total: 1h 49m 15s	remaining: 37.2s
99435:	learn: 0.0756032	total: 1h 49m 15s	remaining: 37.2s
99436:	learn: 0.0756029	total: 1h 49m 15s	remaining: 37.1s
99437:	learn: 0.0756024	total: 1h 49m 15s	remaining: 37s
99438:	learn: 0.0756020	total: 1h 49m 15s	remaining: 37s
99439:	learn: 0.0756016	total: 1h 49m 15s	remaining: 36.9s
99440:	learn: 0.0756014	total: 1h 49m 15s	remaining: 36.9s
99441:	learn: 0.0756011	total: 1h 49m 15s	remaining: 36.8s
99442:	learn: 0.0756001	total: 1h 49m 15s	remaining: 36.7s
99443:	learn: 0.0755998	total: 1h 49m 15s	remaining: 36.7s
99444:	learn: 0.0755993	total: 1h 49m 15s	remaining: 36.6s
99445:	learn: 0.0755990	total: 1h 49m 15s	remaining: 36.5s
99446:	learn: 0.0755988	total: 1h 49m 15s	remaining: 36.5s
99447:	learn: 0.0755983	total: 1h 49m 15s	remaining: 36.4s
9

99576:	learn: 0.0755373	total: 1h 49m 20s	remaining: 27.9s
99577:	learn: 0.0755369	total: 1h 49m 20s	remaining: 27.8s
99578:	learn: 0.0755367	total: 1h 49m 20s	remaining: 27.7s
99579:	learn: 0.0755365	total: 1h 49m 20s	remaining: 27.7s
99580:	learn: 0.0755358	total: 1h 49m 20s	remaining: 27.6s
99581:	learn: 0.0755353	total: 1h 49m 20s	remaining: 27.5s
99582:	learn: 0.0755350	total: 1h 49m 20s	remaining: 27.5s
99583:	learn: 0.0755347	total: 1h 49m 20s	remaining: 27.4s
99584:	learn: 0.0755343	total: 1h 49m 21s	remaining: 27.3s
99585:	learn: 0.0755339	total: 1h 49m 21s	remaining: 27.3s
99586:	learn: 0.0755337	total: 1h 49m 21s	remaining: 27.2s
99587:	learn: 0.0755336	total: 1h 49m 21s	remaining: 27.1s
99588:	learn: 0.0755332	total: 1h 49m 21s	remaining: 27.1s
99589:	learn: 0.0755329	total: 1h 49m 21s	remaining: 27s
99590:	learn: 0.0755325	total: 1h 49m 21s	remaining: 26.9s
99591:	learn: 0.0755320	total: 1h 49m 21s	remaining: 26.9s
99592:	learn: 0.0755316	total: 1h 49m 21s	remaining: 26.8s

99720:	learn: 0.0754702	total: 1h 49m 26s	remaining: 18.4s
99721:	learn: 0.0754700	total: 1h 49m 26s	remaining: 18.3s
99722:	learn: 0.0754693	total: 1h 49m 26s	remaining: 18.2s
99723:	learn: 0.0754686	total: 1h 49m 26s	remaining: 18.2s
99724:	learn: 0.0754683	total: 1h 49m 26s	remaining: 18.1s
99725:	learn: 0.0754678	total: 1h 49m 26s	remaining: 18s
99726:	learn: 0.0754677	total: 1h 49m 26s	remaining: 18s
99727:	learn: 0.0754673	total: 1h 49m 26s	remaining: 17.9s
99728:	learn: 0.0754669	total: 1h 49m 26s	remaining: 17.8s
99729:	learn: 0.0754668	total: 1h 49m 26s	remaining: 17.8s
99730:	learn: 0.0754662	total: 1h 49m 26s	remaining: 17.7s
99731:	learn: 0.0754658	total: 1h 49m 26s	remaining: 17.6s
99732:	learn: 0.0754654	total: 1h 49m 26s	remaining: 17.6s
99733:	learn: 0.0754650	total: 1h 49m 26s	remaining: 17.5s
99734:	learn: 0.0754645	total: 1h 49m 26s	remaining: 17.4s
99735:	learn: 0.0754640	total: 1h 49m 26s	remaining: 17.4s
99736:	learn: 0.0754636	total: 1h 49m 26s	remaining: 17.3s
9

99864:	learn: 0.0754067	total: 1h 49m 32s	remaining: 8.88s
99865:	learn: 0.0754063	total: 1h 49m 32s	remaining: 8.82s
99866:	learn: 0.0754058	total: 1h 49m 32s	remaining: 8.75s
99867:	learn: 0.0754056	total: 1h 49m 32s	remaining: 8.69s
99868:	learn: 0.0754052	total: 1h 49m 32s	remaining: 8.62s
99869:	learn: 0.0754045	total: 1h 49m 32s	remaining: 8.55s
99870:	learn: 0.0754042	total: 1h 49m 32s	remaining: 8.49s
99871:	learn: 0.0754041	total: 1h 49m 32s	remaining: 8.42s
99872:	learn: 0.0754039	total: 1h 49m 32s	remaining: 8.36s
99873:	learn: 0.0754034	total: 1h 49m 32s	remaining: 8.29s
99874:	learn: 0.0754030	total: 1h 49m 32s	remaining: 8.22s
99875:	learn: 0.0754026	total: 1h 49m 32s	remaining: 8.16s
99876:	learn: 0.0754022	total: 1h 49m 32s	remaining: 8.09s
99877:	learn: 0.0754014	total: 1h 49m 32s	remaining: 8.03s
99878:	learn: 0.0754004	total: 1h 49m 32s	remaining: 7.96s
99879:	learn: 0.0753999	total: 1h 49m 32s	remaining: 7.9s
99880:	learn: 0.0753996	total: 1h 49m 32s	remaining: 7.83

#Test Model

In [91]:
predictions = model.predict(X_test)
predictions = [round(value) for value in predictions]
np.unique(predictions , return_counts=True) 

(array([0, 1]), array([ 257, 3179]))

In [96]:
accuracy = accuracy_score(y_test, predictions)
f1_macro = f1_score(y_test, predictions, average='macro')
f1_binary = f1_score(y_test, predictions, average='binary')
print("Accuracy: %.2f%%" % (accuracy * 100.0))
print("Macro F1: %.2f%%" % (f1_macro * 100.0))
print("Binary F1: %.2f%%" % (f1_binary * 100.0))

Accuracy: 97.18%
Macro F1: 91.10%
Binary F1: 98.45%


## Results

### catboost_categorical_100000_epochs_removed_year_month
Accuracy: 97.18%
Macro F1: 91.10%
Binary F1: 98.45%
Submission_Score : 0.97849

### dont know
Accuracy: 96.42%
Macro F1: 88.33%
Binary F1: 98.05%

### catboost with categorical features 100000 epochs 
Accuracy: 96.16%
Macro F1: 86.48%
Binary F1: 97.92%
Submission_score : 0.97375

### catboost without dropping any feature with 400000 epochs

Accuracy: 97.41%
Macro F1: 90.87%
Binary F1: 98.60%
Submission Score : 0.97817

### catboost without dropping any feature  with 100000 epochs

<!-- Accuracy: 97.35%
Macro F1: 90.63%
Binary F1: 98.56%
Submission Score : 0.97848 -->

### catboost after normalizing to z score with 10000 epochs

Accuracy: 96.70%
Macro F1: 87.82%
Binary F1: 98.22%

### catboost without dropping any feature with 10000 epochs

Accuracy: 96.82%
Macro F1: 88.95%
Binary F1: 98.27%
Submission Score : 0.97788

# Save Predictions

In [93]:
predictions_1 = model.predict(test_1)
# predictions_1 = [round(value) for value in y_pred_1]
np.unique(predictions_1 , return_counts=True)

(array([0, 1]), array([ 369, 8207]))

In [94]:
submission_df = pd.read_csv("predications_submission.csv", 
                            index_col="tripid")
submission_df['prediction'] = predictions_1

submission_df.to_csv('predictions/1_catboost_categorical_100000_epochs_removed_year_month.csv')

In [95]:
#  y_pred = pd.DataFrame({'prediction':predictions_1})
#  y_pred["prediction"] = y_pred["prediction"].astype(int)
#  y_pred['prediction'] = y_pred['prediction'].apply(lambda x: 0 if x < 0.5 else 1)
#  y_pred.to_csv("predictions/predications_catboost_6_features_3_100000epochs.csv")
# y_pred.to_csv("/content/drive/My Drive/UNI/SEM7/CS4622_Machine_Learning/Project_1/Fair_Classification/predictions/predications_catboost_6_features_3_400000epochs.csv")